In [49]:
import os
import re
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# ========== 1. 数据目录 ==========
base_dir = "../DATA/Labeled_data/UsingValidationData"
processed_file = os.path.join(base_dir, "processed_results.csv")
summary_file   = os.path.join(base_dir, "model_performance_summary.csv")

# ========== 2. 读入 CSV 数据 ==========
df_folders = pd.read_csv(processed_file)
df_model_avg = pd.read_csv(summary_file, index_col="model_name")

# ========== 3. 手势列表 & 收集 DataFrame ==========
gestures_of_interest = ["ST", "G", "P"]
data_dict = {}

pattern = r"^[^_]+_([^_]+)_.*_([^_]+)$"

for folder in os.listdir(base_dir):
    full_path = os.path.join(base_dir, folder)
    if not os.path.isdir(full_path):
        continue
    
    match = re.match(pattern, folder)
    if not match:
        continue
    
    model_name = match.group(1)
    gesture_name = match.group(2)
    
    if gesture_name not in gestures_of_interest:
        continue
    
    csv_file = os.path.join(full_path, "labeled_modelResult_data.csv")
    if not os.path.isfile(csv_file):
        continue
    
    df_data = pd.read_csv(csv_file)
    
    df_stats = df_folders[df_folders["folder_name"] == folder]
    if len(df_stats) == 0:
        continue
    
    acc_1    = df_stats["accuracy"].iloc[0]
    dly_1    = df_stats["delayed_time"].iloc[0]
    jit_1    = df_stats["jitter_count"].iloc[0]
    
    if model_name not in data_dict:
        data_dict[model_name] = {}
    data_dict[model_name][gesture_name] = {
        "df": df_data,
        "acc": acc_1,
        "delay": dly_1,
        "jitter": jit_1
    }

# ========== 4. 子图网格：行=模型, 列=手势 ==========
all_models = [m for m in df_model_avg.index if m in data_dict]
num_rows = len(all_models)
num_cols = len(gestures_of_interest)

# 设置一个固定的 vertical_spacing（例如 0.1），而不是随 row数而变
fig = make_subplots(
    rows=num_rows,
    cols=num_cols,
    subplot_titles=[f"{m} - {g}" for m in all_models for g in gestures_of_interest],
    vertical_spacing=0.05,    # 行间距固定
    horizontal_spacing=0.03
)

# ========== 5. 绘制每个子图 + 单次指标 ==========
for i, model_name in enumerate(all_models):
    for j, gesture_name in enumerate(gestures_of_interest):
        row_idx = i + 1
        col_idx = j + 1
        
        info = data_dict[model_name].get(gesture_name)
        if info is None:
            continue
        
        df_data = info["df"]
        
        # 只有第一张子图显示图例
        show_legend = (i == 0 and j == 0)
        
        fig.add_trace(
            go.Scatter(
                x=df_data["time"],
                y=df_data["touch_type_idx"],
                mode="lines",
                name="touch_type_idx",
                legendgroup="touch_type_idx",
                showlegend=show_legend,
                line=dict(color="Magenta", width=1),
            ),
            row=row_idx, col=col_idx
        )
        fig.add_trace(
            go.Scatter(
                x=df_data["time"],
                y=df_data["label"],
                mode="lines",
                name="label",
                legendgroup="label",
                showlegend=show_legend,
                line=dict(color="blue", width=1),
            ),
            row=row_idx, col=col_idx
        )

        # 子图左上角写单次 accuracy
        text_1 = (f"Acc={info['acc']:.3f}<br>"
                  f"Delay={info['delay']:.3f}<br>"
                  f"Jitter={info['jitter']:.1f}")
        fig.add_annotation(
            text=text_1,
            x=0.02, y=0.85,
            xref=f"x{row_idx}{col_idx} domain",
            yref=f"y{row_idx}{col_idx} domain",
            showarrow=False,
            font=dict(size=12, color="black"),
            row=row_idx, col=col_idx
        )

# ========== 6. 每行下方标注模型平均值 ==========
for i, model_name in enumerate(all_models):
    subplot_id = i * num_cols + 1
    yaxis_name = "yaxis" + (str(subplot_id) if subplot_id > 1 else "")
    if yaxis_name not in fig.layout:
        continue
    
    avg_acc    = df_model_avg.loc[model_name, "accuracy"]
    avg_delay  = df_model_avg.loc[model_name, "delayed_time"]
    avg_jitter = df_model_avg.loc[model_name, "jitter_count"]
    avg_text   = f"【{model_name}平均】Acc={avg_acc:.3f}, Delay={avg_delay:.3f}, Jitter={avg_jitter:.1f}"

    # 该行子图 domain 的下界
    y_bottom = fig.layout[yaxis_name].domain[0]
    
    # 留更大的空隙，比如 0.04，配合大的 margin["b"]
    y_annot = y_bottom - 0.04
    
    fig.add_annotation(
        text=avg_text,
        x=0.5,
        y=y_annot,
        xref="paper",
        yref="paper",
        showarrow=False,
        font=dict(size=16, color="blue"),
        align="center"
    )

# ========== 7. 全局布局 ==========
# 调大 top 和 bottom，给大标题、图例、以及底部注释留空间
fig.update_layout(
    title=dict(
        text="Model Summary",
        x=0.5,
        y=0.98,
        xanchor="center",
        yanchor="top",
        font=dict(size=24, color="black")
    ),
    legend=dict(
        orientation="h",
        x=0.5,
        y=0.92,            # 可以比 1.0 略低，避免贴边
        xanchor="center",
        yanchor="top",
        font=dict(size=12)
    ),
    margin=dict(t=180, b=200, l=50, r=50),  # 上方/下方留大空间
    height=300 * num_rows + 100,
    width=400 * num_cols,
    hovermode="x unified"
)

fig.show()
